In [3]:
#@title Imports
!pip install unidecode
!pip install ibge
# Facilitador para obter dados IBGE
import ibge

import json
import pandas as pd
import numpy as np

# PLN
from natsort import natsorted
from unidecode import unidecode

# Mapas interativos
import folium as fl
from folium.plugins import MarkerCluster
from folium.plugins import FastMarkerCluster
from google.colab import drive

### **Upload bases**

In [16]:
# Clonar o repositório do GitHub
!git clone https://github.com/MurilloYumoto/Analise-Criminal-no-Brasil.git

# Mudar para o diretório do repositório clonado
%cd Analise-Criminal-no-Brasil

# Baixar o arquivo CSV
!wget -q https://raw.githubusercontent.com/MurilloYumoto/Analise-Criminal-no-Brasil/main/Mapas-IDHM/dados_idhm_por_municipio%20-%20Worksheet.csv -O dados_idhm_por_municipio.csv

# Baixar o arquivo JSON
!wget -q https://raw.githubusercontent.com/MurilloYumoto/Analise-Criminal-no-Brasil/main/Mapas-IDHM/geojs-35-mun.json -O geojs-35-mun.json

Cloning into 'Analise-Criminal-no-Brasil'...
remote: Enumerating objects: 62, done.
remote: Counting objects: 100% (62/62), done.
remote: Compressing objects: 100% (50/50), done.
remote: Total 62 (delta 22), reused 39 (delta 7), pack-reused 0 (from 0)
Receiving objects: 100% (62/62), 804.43 KiB | 4.30 MiB/s, done.
Resolving deltas: 100% (22/22), done.
/content/Analise-Criminal-no-Brasil/Analise-Criminal-no-Brasil/Analise-Criminal-no-Brasil


### **Mapas**

In [17]:
#@title Base IDHM

df = pd.read_csv('/content/dados_idhm_por_municipio - Worksheet.csv')

# Removendo o IDH do Estado do índice
df = df.iloc[2:-1,:]
df.reset_index(drop=True, inplace=True)

# Processando os nomes dos municípios
df['Territorialidades'] = df['Territorialidades'].str.split('(').str[0]
df['IDHM 2010'] = df['IDHM 2010'].str.replace(',','.')
df['IDHM 2010'] = df['IDHM 2010'].astype(float)

df['IDHM Renda 2010'] = df['IDHM Renda 2010'].str.replace(',','.')
df['IDHM Renda 2010'] = df['IDHM Renda 2010'].astype(float)

df['IDHM Longevidade 2010'] = df['IDHM Longevidade 2010'].str.replace(',','.')
df['IDHM Longevidade 2010'] = df['IDHM Longevidade 2010'].astype(float)

df['IDHM Educação 2010'] = df['IDHM Educação 2010'].str.replace(',','.')
df['IDHM Educação 2010'] = df['IDHM Educação 2010'].astype(float)

df['Territorialidades'] = df['Territorialidades'].astype(str)

df

Territorialidades  IDHM 2010  IDHM Renda 2010  IDHM Longevidade 2010  \
0              Adamantina       0.790            0.772                  0.852   
1                  Adolfo       0.730            0.710                  0.844   
2                   Aguaí       0.715            0.703                  0.858   
3          Águas da Prata       0.781            0.750                  0.886   
4        Águas de Lindóia       0.745            0.725                  0.846   
..                     ...        ...              ...                    ...   
640  Vista Alegre do Alto       0.744            0.726                  0.840   
641        Vitória Brasil       0.725            0.686                  0.811   
642            Votorantim       0.767            0.720                  0.838   
643           Votuporanga       0.790            0.772                  0.857   
644              Zacarias       0.729            0.695                  0.826   

     IDHM Educação 2010  
0                 0.750  
1                 0.648  
2                 0.606  
3                 0.716  
4                 0.675  
..                  ...  
640               0.676  
641               0.685  
642               0.747  
643               0.744  
644               0.674  

[645 rows x 5 columns]

In [7]:
#@title Manipulação da base dos municípios
from ibge.localidades import *

data = Municipios()
municipios = pd.DataFrame(data.getDados())
municipios_sp = municipios[municipios['uf']=='SP']
municipios_sp = municipios_sp.drop(columns = 'uf')
municipios_sp['cod'] = municipios_sp['ibge']
municipios_sp = municipios_sp.drop(columns = 'ibge')

# Ordenar sem levar os acentos em consideração
municipios_sp['nome_ordenacao'] = municipios_sp['nome'].apply(unidecode)
municipios_sp.sort_values('nome_ordenacao', inplace=True)

municipios_sp.reset_index(drop=True, inplace=True)
municipios_sp

nome      cod        nome_ordenacao
0              Adamantina  3500105            Adamantina
1                  Adolfo  3500204                Adolfo
2                   Aguaí  3500303                 Aguai
3          Águas da Prata  3500402        Aguas da Prata
4        Águas de Lindóia  3500501      Aguas de Lindoia
..                    ...      ...                   ...
640  Vista Alegre do Alto  3556909  Vista Alegre do Alto
641        Vitória Brasil  3556958        Vitoria Brasil
642            Votorantim  3557006            Votorantim
643           Votuporanga  3557105           Votuporanga
644              Zacarias  3557154              Zacarias

[645 rows x 3 columns]

In [18]:
#@title Junção das bases
df_final = df.join(municipios_sp[['cod', 'nome_ordenacao']])
df_final

Territorialidades  IDHM 2010  IDHM Renda 2010  IDHM Longevidade 2010  \
0              Adamantina       0.790            0.772                  0.852   
1                  Adolfo       0.730            0.710                  0.844   
2                   Aguaí       0.715            0.703                  0.858   
3          Águas da Prata       0.781            0.750                  0.886   
4        Águas de Lindóia       0.745            0.725                  0.846   
..                     ...        ...              ...                    ...   
640  Vista Alegre do Alto       0.744            0.726                  0.840   
641        Vitória Brasil       0.725            0.686                  0.811   
642            Votorantim       0.767            0.720                  0.838   
643           Votuporanga       0.790            0.772                  0.857   
644              Zacarias       0.729            0.695                  0.826   

     IDHM Educação 2010      cod        nome_ordenacao  
0                 0.750  3500105            Adamantina  
1                 0.648  3500204                Adolfo  
2                 0.606  3500303                 Aguai  
3                 0.716  3500402        Aguas da Prata  
4                 0.675  3500501      Aguas de Lindoia  
..                  ...      ...                   ...  
640               0.676  3556909  Vista Alegre do Alto  
641               0.685  3556958        Vitoria Brasil  
642               0.747  3557006            Votorantim  
643               0.744  3557105           Votuporanga  
644               0.674  3557154              Zacarias  

[645 rows x 7 columns]

## **IDHM por município**

In [19]:
#@title Mapa IDHM por município

state_geo = '/content/Analise-Criminal-no-Brasil/Mapas-IDHM/geojs-35-mun.json'

map = fl.Map(location=[-23.53, -46.8], width=900,height=500, zoom_start=6)

#Criar a camada Choroplet
fl.Choropleth(
    geo_data=state_geo,
    name='choropleth',
    data=df_final,
    columns=['cod', 'IDHM 2010'],
    key_on='feature.properties.id',
    fill_color='GnBu',
    fill_opacity=0.7,
    line_opacity=0.1,
    legend_name='IDHM por município'
).add_to(map)

map

In [21]:
#@title Mapa IDHM por muninicípio com marcadores

with open('/content/Analise-Criminal-no-Brasil/Mapas-IDHM/geojs-35-mun.json', 'r') as file:
    geo_data = json.load(file)

def get_centroid(geometry):
    coordinates = geometry['coordinates'][0]
    lat = [point[1] for point in coordinates]
    lon = [point[0] for point in coordinates]
    return [sum(lat) / len(lat), sum(lon) / len(lon)]

idhm_dict = dict(zip(df_final['nome_ordenacao'], df_final['IDHM 2010']))

# Adicionar os marcadores
for feature in geo_data['features']:
    nome_municipio = feature['properties']['name']
    nome_sem_acento = unidecode(nome_municipio)
    centroid = get_centroid(feature['geometry'])

    match = df_final[df_final['nome_ordenacao'] == nome_sem_acento]

    if not match.empty:
        idhm = match['IDHM 2010'].values[0]
        idhm_edu = match['IDHM Educação 2010'].values[0]
        idhm_renda = match['IDHM Renda 2010'].values[0]
        idhm_longev = match['IDHM Longevidade 2010'].values[0]
    else:
        # Caso não encontre correspondência
        idhm = "IDHM não disponível"
        idhm_edu = "IDHME não disponível"
        idhm_renda = "IDHMR não disponível"
        idhm_longev = "IDHML não disponível"

    popup_text = (
        f"{nome_municipio}<br>"
        f"IDHM: {idhm}<br>"
        f"IDHME: {idhm_edu}<br>"
        f"IDHMR: {idhm_renda}<br>"
        f"IDHML: {idhm_longev}"
    )
    fl.Marker(
        location=centroid,
        popup=popup_text,
        icon=fl.Icon(color='blue', icon='info-sign')
    ).add_to(map)

map

## **IPDM**